In [48]:
import os
import glob
import time
from datetime import timedelta, datetime
import numpy as np
import pandas as pd
import qgrid

from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import gezi

from projects.feed.rank.monitor.taurus import Taurus

In [49]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [50]:
last_days = 80
start_time = None
end_time = None
# start_time = 20191210
# end_time = 20191220
# abids = [8,15,16]
# abids = [16, 8]
# abids = [16]
# abids = [8, 15]
# abids = [15]
# abids = [8]
abids = [16]
abids = [11]

assert len(abids) < 2, 'FIXME only 1 abid is ok now, as natural_diff wrong currenlty TODO'
product = 'sgsapp'
# product = 'newmse'

diff_spans_ = {
    8: [20200313, 20200319],
#     12: [20190130, 20200205],
#     11: [20190130, 20200205],
    10: [20200325, 20200331],
    11: [20200325, 20200331],
    15: [20200325, 20200331],
    16: [20200325, 20200331],
    17: [20200325, 20200331],
}
diff_spans = {}
for abid in abids:
  diff_spans[abid] = diff_spans_[abid]

diff_spans = None

In [51]:
worker_daily = Taurus()
worker_daily.init(abids, last_days, 'daily', product=product,
                  diff_spans=diff_spans, start_time=start_time, end_time=end_time)
worker_daily.run()

# for name 1(tuwen,video,small_video,total) 2(quality,total) 3(recommend,relative,total)
def show_daily(name, use_diff=True, quality=False, field=None):
  worker_daily.show(name, quality, field, use_diff=False)

SELECT * FROM feed_abtest_video_type_common_daily 
                WHERE product = 'sgsapp'
                AND abtest in ('5','4','11','6') 
                AND date BETWEEN '20200702' AND '20200921'
                AND video_type in ('0', '1', '2', 'total')
          
/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

28.26490354537964


In [62]:
w = worker_daily
d = worker_daily.ratio2
d = d.sort_values('date', ascending=False)
# pd.set_option('precision', 5)  
names = ['dis_user', 'click_user', 'click', 'duration', 'refresh_times', 'read_files', 'ctr', 'read_ratio', 'dur1', 'dur2', 
         'doc_dur', 'finish_ratio', 'praise', 'favor', 'share']
# d2 = d[d.name!='small_video'].groupby(['name', 'data_obj', 'abtest']).head(6).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]
d2 = d.groupby(['name', 'data_obj', 'abtest']).head(7).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]

# qgrid.show_grid(d2)
# d.groupby(['name', 'data_obj', 'abtest']).head(1)

In [63]:
d_ = d2[d2.data_obj=='total_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [64]:
d_ = d2[d2.data_obj=='quality_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [65]:
d_ = d2[d2.data_obj=='total_relative']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [66]:
w.ratio2[w.ratio2.name=='video'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
1919  20200920  0.010362    0.022699  0.067157  0.026591       0.013288   
1895  20200919  0.010907    0.002526  0.040652  0.001196       0.052031   
1871  20200918  0.015420    0.023295  0.071699  0.022669       0.037826   
1847  20200917  0.012591    0.008559  0.076859  0.023388       0.029705   
1823  20200916  0.013356    0.026807  0.025521  0.060902       0.033825   
...        ...       ...         ...       ...       ...            ...   
116   20200706  0.011791    0.016362 -0.003399  0.003471       0.012817   
92    20200705  0.009480    0.005006  0.005576  0.022475      -0.001949   
68    20200704  0.007699    0.005557  0.025503  0.048784       0.001144   
44    20200703  0.011491    0.018711 -0.005139  0.008912       0.014161   
20    20200702  0.009000    0.018445  0.015619  0.014180       0.020035   

      read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
1919    0.056226  0.045970    0.012209  0.016074  0.003850 -0.037970   
1895    0.029452  0.030791   -0.008280 -0.009579 -0.001288 -0.037915   
1871    0.055448  0.040164    0.007765  0.007160 -0.000589 -0.045828   
1847    0.063467  0.046631   -0.003983  0.010705  0.014765 -0.049588   
1823    0.012008  0.008837    0.013267  0.046950  0.033214  0.034527   
...          ...       ...         ...       ...       ...       ...   
116    -0.015029 -0.017301    0.004518 -0.008237 -0.012770  0.006889   
92     -0.003844 -0.000763   -0.004429  0.012887  0.017395  0.016781   
68      0.017666  0.002274   -0.002131  0.040778  0.043026  0.022358   
44     -0.016429 -0.032890    0.007142 -0.002552 -0.009605  0.014008   
20      0.006608 -0.007656    0.009358  0.005143 -0.004221 -0.001541   

      finish_ratio    praise     favor     share  
1919      0.068923  0.018486 -0.232418  0.131818  
1895      0.086264 -0.153864 -0.148440  0.258537  
1871      0.122847 -0.122318 -0.252990  0.349206  
1847      0.093138 -0.097885  0.038355 -0.227273  
1823     -0.072852 -0.132463 -0.041602  0.000000  
...            ...       ...       ...       ...  
116      -0.007632  0.095331  0.317668 -0.137500  
92        0.013222  0.002709  0.017728  0.024615  
68        0.034708  0.033070  0.347721 -0.150602  
44       -0.005265  0.151175 -0.043578 -0.215232  
20        0.001608  0.032181  0.181364 -0.023810  

[79 rows x 16 columns]

In [67]:
w.ratio2[w.ratio2.name=='tuwen'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
1913  20200920  0.010139    0.003760  0.015419  0.024395       0.015472   
1889  20200919  0.012485    0.003370 -0.004686 -0.001819      -0.016292   
1865  20200918  0.015545    0.026753  0.029978  0.048259       0.008910   
1841  20200917  0.012484    0.020436  0.036592  0.038393       0.008958   
1817  20200916  0.013314    0.010946  0.014062  0.019849       0.005025   
...        ...       ...         ...       ...       ...            ...   
110   20200706  0.012944    0.005186  0.017985  0.031491       0.010456   
86    20200705  0.009217    0.000663  0.004962  0.011832       0.018840   
62    20200704  0.009086    0.013279  0.032043  0.036098       0.028391   
38    20200703  0.011586    0.013559  0.051490  0.056158       0.033627   
14    20200702  0.008768    0.014708  0.024540  0.034211       0.024747   

      read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
1913    0.005228 -0.000325   -0.006318  0.014112  0.020545  0.008829   
1889   -0.016981 -0.005604   -0.009002 -0.014133 -0.005186  0.002861   
1865    0.014182  0.013945    0.011024  0.032183  0.020899  0.017748   
1841    0.023773  0.019168    0.007846  0.025583  0.017604  0.001700   
1817    0.000695  0.002415   -0.002346  0.006402  0.008799  0.005699   
...          ...       ...         ...       ...       ...       ...   
110     0.004969  0.006474   -0.007652  0.018300  0.026103  0.013203   
86     -0.004226 -0.007816   -0.008471  0.002577  0.011123  0.006794   
62      0.022780  0.007460    0.004159  0.026787  0.022559  0.003856   
38      0.039446  0.018485    0.001955  0.044058  0.041986  0.004402   
14      0.015638  0.000616    0.005894  0.025206  0.019194  0.009410   

      finish_ratio    praise     favor     share  
1913      0.008953  0.243217 -0.023241  0.003626  
1889      0.007532  0.395665 -0.052367  0.040984  
1865      0.006344  0.684143 -0.016814  0.270010  
1841      0.003607  0.398236  0.041703  0.240084  
1817      0.000575  0.730847 -0.014460  0.218045  
...            ...       ...       ...       ...  
110       0.000630  0.109404  0.015809 -0.189767  
86       -0.003534  0.314712  0.103365  0.002791  
62        0.007714  0.332916  0.045293 -0.037500  
38       -0.000269  0.179343  0.080064  0.083821  
14        0.006933  0.109294 -0.016633  0.056733  

[79 rows x 16 columns]

In [68]:
w.ratio2[w.ratio2.name=='total'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
1907  20200920  0.010252    0.012295  0.054864  0.025810       0.014810   
1883  20200919  0.012133    0.005154  0.030890  0.000325       0.003547   
1859  20200918  0.015326    0.024764  0.061672  0.030246       0.017330   
1835  20200917  0.012318    0.014684  0.066833  0.027709       0.015556   
1811  20200916  0.013499    0.012994  0.022805  0.048416       0.013881   
...        ...       ...         ...       ...       ...            ...   
104   20200706  0.012460    0.007261  0.002393  0.014126       0.010876   
80    20200705  0.009016    0.000278  0.006835  0.019188       0.011822   
56    20200704  0.008427    0.010243  0.027184  0.044299       0.019742   
32    20200703  0.011401    0.010788  0.008193  0.026496       0.026925   
8     20200702  0.009214    0.014408  0.020230  0.022266       0.022742   

      read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
1907    0.044169  0.036684    0.002022  0.015409  0.013362 -0.027532   
1883    0.018551  0.025679   -0.006896 -0.011648 -0.004788 -0.029647   
1859    0.045656  0.038364    0.009287  0.014702  0.005339 -0.029657   
1835    0.053842  0.043362    0.002330  0.015229  0.012881 -0.036631   
1811    0.009175  0.008949   -0.000505  0.034455  0.034960  0.025034   
...          ...       ...         ...       ...       ...       ...   
104    -0.009956 -0.011049   -0.005130  0.001630  0.006765  0.011701   
80     -0.002145 -0.002897   -0.008655  0.010085  0.018903  0.012246   
56      0.018608  0.002807    0.001803  0.035585  0.033746  0.016440   
32     -0.003166 -0.022531   -0.000603  0.014921  0.015544  0.018083   
8       0.010952 -0.003572    0.005153  0.012934  0.007739  0.001899   

      finish_ratio    praise     favor     share  
1907      0.005890  0.100826 -0.073218  0.024943  
1883      0.014129  0.015457 -0.078767  0.073563  
1859      0.019167  0.169643 -0.080406  0.281174  
1835      0.014341  0.088318  0.041333  0.156627  
1811     -0.018029  0.211665 -0.019835  0.181737  
...            ...       ...       ...       ...  
104       0.006319  0.081551  0.081243 -0.181233  
80        0.002172  0.151829  0.079669 -0.011706  
56        0.018452  0.148481  0.112944 -0.059222  
32        0.024632  0.152296  0.047845  0.033641  
8         0.011242  0.093640  0.025916  0.045797  

[81 rows x 16 columns]

In [69]:
w.df[w.df.name=='total'][w.df.data_obj=='total_total']

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



product_name      date   name     data_obj  abtest        id         dis  \
11         sgsapp  20200702  total  total_total      11  33202687  33746668.0   
35         sgsapp  20200703  total  total_total      11  33376321  34641308.0   
59         sgsapp  20200704  total  total_total      11  33550223  33054656.0   
83         sgsapp  20200705  total  total_total      11  33725007  33694046.0   
107        sgsapp  20200706  total  total_total      11  33898109  32693802.0   
...           ...       ...    ...          ...     ...       ...         ...   
1814       sgsapp  20200916  total  total_total      11  47893289  23339992.0   
1838       sgsapp  20200917  total  total_total      11  48111989  23420134.0   
1862       sgsapp  20200918  total  total_total      11  48331255  23803900.0   
1886       sgsapp  20200919  total  total_total      11  48553441  24928866.0   
1910       sgsapp  20200920  total  total_total      11  48776019  25219744.0   

      dis_user  refresh_times   real_dis  ...       ctr  real_ctr  read_ratio  \
11    296728.0      1358224.0  7445470.0  ...  0.057213  0.259317    0.343621   
35    300716.0      1475250.0  7537322.0  ...  0.056802  0.261060    0.345675   
59    302948.0      1428744.0  7079938.0  ...  0.064823  0.302646    0.337979   
83    308314.0      1449862.0  7146424.0  ...  0.066616  0.314080    0.338888   
107   298346.0      1428356.0  7035120.0  ...  0.062783  0.291768    0.341248   
...        ...            ...        ...  ...       ...       ...         ...   
1814  288346.0      1400504.0  6956766.0  ...  0.087521  0.293634    0.378372   
1838  281510.0      1397852.0  7073038.0  ...  0.090677  0.300248    0.378075   
1862  292022.0      1418856.0  7197884.0  ...  0.091001  0.300946    0.387608   
1886  303304.0      1472698.0  7465052.0  ...  0.098258  0.328124    0.385877   
1910  299116.0      1483706.0  7590356.0  ...  0.098253  0.326456    0.392156   

          dur1       dur2  finish_ratio  read_files   doc_dur   refresh  \
11    6.784983  19.745537      0.258934    6.506767  1.042758  4.577337   
35    6.915517  20.005835      0.255113    6.543350  1.056877  4.905792   
59    7.096432  20.996678      0.245938    7.072890  1.003328  4.716136   
83    7.207987  21.269509      0.245386    7.280065  0.990099  4.702550   
107   6.655455  19.503274      0.251221    6.880019  0.967360  4.787582   
...        ...        ...           ...         ...       ...       ...   
1814  8.431659  22.284057      0.215883    7.084357  1.190180  4.857026   
1838  8.712585  23.044571      0.219689    7.543846  1.154926  4.965550   
1862  8.454562  21.812157      0.219292    7.417838  1.139761  4.858730   
1886  8.834952  22.895780      0.209214    8.075924  1.093987  4.855518   
1910  9.236836  23.554012      0.211597    8.284144  1.115002  4.960303   

       refresh2  
11    13.320884  
35    14.191919  
59    13.953941  
83    13.876402  
107   14.029624  
...         ...  
1814  12.836648  
1838  13.133757  
1862  12.535171  
1886  12.583076  
1910  12.648815  

[81 rows x 33 columns]

In [70]:
w.base[w.base.name=='video'][w.base.data_obj=='total_total']

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



product_name      date   name     data_obj  abtest          id  \
23         sgsapp  20200702  video  total_total     5.0  33202329.0   
47         sgsapp  20200703  video  total_total     5.0  33375939.0   
71         sgsapp  20200704  video  total_total     5.0  33549811.0   
95         sgsapp  20200705  video  total_total     5.0  33724601.0   
119        sgsapp  20200706  video  total_total     5.0  33897715.0   
...           ...       ...    ...          ...     ...         ...   
1826       sgsapp  20200916  video  total_total     5.0  47892937.0   
1850       sgsapp  20200917  video  total_total     5.0  48111607.0   
1874       sgsapp  20200918  video  total_total     5.0  48330845.0   
1898       sgsapp  20200919  video  total_total     5.0  48553053.0   
1922       sgsapp  20200920  video  total_total     5.0  48775601.0   

               dis       dis_user  refresh_times      real_dis  ...       ctr  \
23    1.691364e+07  290232.000000  627249.333333  2.585670e+06  ...  0.078435   
47    1.717905e+07  293252.000000  640526.666667  2.607195e+06  ...  0.080251   
71    1.738699e+07  295878.000000  624670.666667  2.611128e+06  ...  0.088687   
95    1.787957e+07  300675.333333  653165.333333  2.673109e+06  ...  0.091877   
119   1.602295e+07  291612.666667  631146.000000  2.621317e+06  ...  0.091744   
...            ...            ...            ...           ...  ...       ...   
1826  1.060346e+07  279330.000000  479232.666667  2.419729e+06  ...  0.143263   
1850  1.067514e+07  273177.333333  480043.333333  2.424138e+06  ...  0.140921   
1874  1.081045e+07  282720.666667  455229.333333  2.406071e+06  ...  0.142264   
1898  1.165335e+07  293786.000000  433582.000000  2.535459e+06  ...  0.158822   
1922  1.167222e+07  291183.333333  385670.000000  2.501514e+06  ...  0.155728   

      real_ctr  read_ratio      dur1       dur2  finish_ratio  read_files  \
23    0.513054    0.226411  3.997291  17.656448      0.119693    4.570731   
47    0.528796    0.232718  4.090034  17.575123      0.119105    4.701189   
71    0.590629    0.233290  4.352942  18.658714      0.119191    5.211821   
95    0.614578    0.234154  4.556116  19.458035      0.123852    5.463337   
119   0.560784    0.229515  3.990053  17.384542      0.121667    5.040771   
...        ...         ...       ...        ...           ...         ...   
1826  0.627792    0.234157  5.832624  24.908347      0.110720    5.438400   
1850  0.620570    0.234727  6.249566  26.623572      0.103575    5.507045   
1874  0.639194    0.235301  6.026211  25.611327      0.100063    5.439788   
1898  0.729975    0.242269  6.551150  27.040557      0.101705    6.299962   
1922  0.726651    0.241321  6.701313  27.768286      0.099022    6.242406   

       doc_dur   refresh  refresh2  
23    0.874554  2.161217  9.546070  
47    0.870080  2.184234  9.385900  
71    0.835397  2.111307  9.050421  
95    0.833942  2.172359  9.277715  
119   0.791541  2.164338  9.430075  
...        ...       ...       ...  
1826  1.072460  1.715658  7.327004  
1850  1.134800  1.757268  7.486608  
1874  1.107807  1.610207  6.843366  
1898  1.039895  1.475836  6.091722  
1922  1.073470  1.324493  5.488598  

[80 rows x 33 columns]

In [71]:
show_daily('total_quality_total')

In [72]:
show_daily('total_quality_total')

In [73]:
show_daily('tuwen_quality_total')

In [ ]:
show_daily('video_total_recommend')

In [45]:
show_daily('video_total_relative')

refresh_times with same vals ignore


In [46]:
show_daily('tuwen_total_total')

In [47]:
w.ratio

product_name      date         name           data_obj  abtest        id  \
0          sgsapp  20200701  small_video  quality_recommend      11 -0.000004   
1          sgsapp  20200701  small_video   quality_relative      11 -0.000004   
2          sgsapp  20200701  small_video      quality_total      11 -0.000004   
3          sgsapp  20200701  small_video    total_recommend      11 -0.000004   
4          sgsapp  20200701  small_video     total_relative      11 -0.000004   
...           ...       ...          ...                ...     ...       ...   
1918       sgsapp  20200919        video   quality_relative      11 -0.000002   
1919       sgsapp  20200919        video      quality_total      11 -0.000002   
1920       sgsapp  20200919        video    total_recommend      11 -0.000002   
1921       sgsapp  20200919        video     total_relative      11 -0.000002   
1922       sgsapp  20200919        video        total_total      11 -0.000002   

           dis  dis_user  refresh_times  real_dis  ...       ctr  real_ctr  \
0     0.046877  0.019345      -0.577465  0.050059  ... -0.106728 -0.109487   
1    -0.141276 -0.001715       0.000000  0.000000  ... -0.043304 -0.184936   
2     0.036216  0.012650      -0.049901  0.049980  ... -0.195098 -0.206107   
3     0.010343  0.010773       0.235294  0.007871  ... -0.056507 -0.053954   
4    -0.028017 -0.020197       0.000000  0.000000  ... -0.011684 -0.041899   
...        ...       ...            ...       ...  ...       ...       ...   
1918  0.013202  0.005025       0.000000  0.000000  ...  0.037628  0.051306   
1919  0.009605  0.010907       0.052031  0.020602  ...  0.030791  0.019586   
1920  0.009450  0.011043       0.051339  0.020270  ... -0.025324 -0.035650   
1921  0.013571  0.009576       0.000000  0.069887  ...  0.022124 -0.032428   
1922  0.010729  0.010545       0.048526  0.019926  ...  0.016019  0.006851   

      read_ratio      dur1      dur2  finish_ratio  read_files   doc_dur  \
0       0.047910 -0.159114 -0.202773     -0.112144   -0.081623 -0.097071   
1      -0.039368 -0.238261 -0.208578     -0.267637   -0.187992 -0.061214   
2      -0.029436 -0.234774 -0.218410     -0.232869   -0.177570 -0.065675   
3       0.001021 -0.113695 -0.114886     -0.038250   -0.056524 -0.065935   
4      -0.082953  0.047451  0.144577     -0.091790   -0.022429  0.073989   
...          ...       ...       ...           ...         ...       ...   
1918   -0.005655 -0.008338 -0.002666      0.076151    0.046074 -0.052002   
1919   -0.008280 -0.009579 -0.001288      0.086264    0.029452 -0.037915   
1920   -0.003196  0.022567  0.025849     -0.066090   -0.026871  0.050773   
1921   -0.008957 -0.027564 -0.018777      0.059798    0.026161 -0.052378   
1922   -0.003391 -0.018275 -0.014927      0.060664    0.016187 -0.033935   

       refresh  refresh2  
0    -0.587015 -0.589993  
1    -0.011897  0.029366  
2    -0.061608 -0.046082  
3     0.222220  0.219454  
4     0.020589  0.112117  
...        ...       ...  
1918 -0.005006  0.000553  
1919  0.040697  0.049414  
1920  0.039858  0.043186  
1921 -0.009490 -0.000596  
1922  0.037589  0.041119  

[1923 rows x 33 columns]